# Atividade 2 - Spark

Esse notebook é baseado no notebook [como instalar pyspark no google colab](https://colab.research.google.com/github/carlosfab/sigmoidal_ai/blob/master/Big_Data_Como_instalar_o_PySpark_no_Google_Colab.ipynb).

O ambiente de execução é configurado para executar no Google Colab.

## Configuração do Spark para Google Colab

In [4]:
# instalar as dependências
!apt-get update
!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget -q https://archive.apache.org/dist/spark/spark-2.4.4/spark-2.4.4-bin-hadoop2.7.tgz
!tar xf spark-2.4.4-bin-hadoop2.7.tgz
!pip install -q findspark

Ign:1 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Get:2 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Ign:3 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Get:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release [696 B]
Hit:5 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Hit:6 http://archive.ubuntu.com/ubuntu bionic InRelease
Get:7 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease [15.9 kB]
Get:8 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release.gpg [836 B]
Get:9 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease [3,626 B]
Get:10 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Hit:12 http://ppa.launchpad.net/cran/libgit2/ubuntu bionic InRelease
Get:13 https://developer.download.nvidia.com/compute/c

In [8]:
# configurar as variáveis de ambiente
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-2.4.4-bin-hadoop2.7"

# tornar o pyspark "importável"
import findspark
findspark.init('spark-2.4.4-bin-hadoop2.7')

import pyspark

## Exercicios da Atividade 2

### 1. Utilizando o dataset flights.csv, faça operações MapReduce para calcular:

Importação do arquivo necessario para atividade

In [9]:
sc = pyspark.SparkContext(appName='BigDataAtividade2')

flights_file = '/content/flights.csv'
flights_RDD = sc.textFile(flights_file)
print("dataVoo	id_companhia	num_voos	origem	destino	hora_partida	min_atraso	hora_chegada	min_atraso	duracao	distancia")
print(flights_RDD.take(1))


dataVoo	id_companhia	num_voos	origem	destino	hora_partida	min_atraso	hora_chegada	min_atraso	duracao	distancia
['2014-04-01,19805,1,JFK,LAX,0854,-6.00,1217,2.00,355.00,2475.00']


a. O tempo total de vôo de cada companhia

In [10]:
def tempo_total_de_voo_por_companhia(line):
    record = line.split(',')
    return (record[1],float(record[9]))

voos = flights_RDD.map(tempo_total_de_voo_por_companhia).reduceByKey(lambda a,b: a+b).take(10)

for voo in voos:
  print(f'Companhia: {voo[0]}, tempo total de voo: {voo[1]}')

Companhia: 19930, tempo total de voo: 2001295.0
Companhia: 20409, tempo total de voo: 3009096.0
Companhia: 20366, tempo total de voo: 4142864.0
Companhia: 20437, tempo total de voo: 799733.0
Companhia: 19690, tempo total de voo: 449242.0
Companhia: 20355, tempo total de voo: 4194811.0
Companhia: 21171, tempo total de voo: 916098.0
Companhia: 19805, tempo total de voo: 6273366.0
Companhia: 19790, tempo total de voo: 7747256.0
Companhia: 20436, tempo total de voo: 689589.0


b. Qual é o destino mais visado

In [11]:
def destino_mais_visado(line):
    record = line.split(',')
    return (record[4],int(1))

destino_mais_visado_RDD = flights_RDD.map(destino_mais_visado)
total_destino_mais_visado = destino_mais_visado_RDD.reduceByKey(lambda a,b: a+b).take(500000)

print(f'Quantidade total de destinos: {len(total_destino_mais_visado)}')

destino_mais_visitado = ('', 0)

for destino in total_destino_mais_visado:
  if destino[1] > destino_mais_visitado[1]:
    destino_mais_visitado = destino

print(f'O destino mais visado foi {destino_mais_visitado[0]}, com {destino_mais_visitado[1]} visitas.')

Quantidade total de destinos: 304
O destino mais visado foi ATL, com 30953 visitas.


c. Quais aeroportos cada companhia passou

In [12]:
def aeroportos_de_origem(line):
    record = line.split(',')
    return (record[1],record[3])

def aeroportos_de_destino(line):
    record = line.split(',')
    return (record[1],record[4])

origens = flights_RDD.map(aeroportos_de_origem).take(50000)
destinos = flights_RDD.map(aeroportos_de_destino).take(50000)

origens_RDD = sc.parallelize(origens)
destinos_RDD = sc.parallelize(destinos)

grouped_elementsDestino = origens_RDD.union(destinos_RDD).distinct().groupByKey().take(50000)

for key, values in grouped_elementsDestino:
    print(key, list(values))

19930 ['DCA', 'EWR', 'BOS', 'PDX', 'FLL', 'ADQ', 'FAI', 'PSP', 'SNA', 'ONT', 'PHX', 'AUS', 'ATL', 'PHL', 'ANC', 'SCC', 'BRW', 'KTN', 'CDV', 'SIT', 'WRG', 'PSG', 'SAN', 'OAK', 'SMF', 'BUR', 'BLI', 'DFW', 'SLC', 'STL', 'SEA', 'LAX', 'ORD', 'MSP', 'JNU', 'YAK', 'OME', 'OTZ', 'SFO', 'LAS', 'DEN', 'IAH', 'KOA', 'ADK', 'MCO', 'BET', 'SJC', 'TUS', 'SAT', 'GEG', 'MCI', 'OGG', 'LIH', 'HNL']
20409 ['DCA', 'FLL', 'BOS', 'SJU', 'SWF', 'EWR', 'JAX', 'CLT', 'TPA', 'HOU', 'BTV', 'CHS', 'DTW', 'RIC', 'SAV', 'AUS', 'BQN', 'PVD', 'PHX', 'PDX', 'SRQ', 'PHL', 'BUF', 'STX', 'HPN', 'DFW', 'BWI', 'SAN', 'PWM', 'LGA', 'OAK', 'SMF', 'SLC', 'ABQ', 'BUR', 'STT', 'RSW', 'PBI', 'IAD', 'ORH', 'PIT', 'ORD', 'ROC', 'LAS', 'LGB', 'DEN', 'SEA', 'SFO', 'LAX', 'JFK', 'MCO', 'MSY', 'RDU', 'SYR', 'BDL', 'PSE', 'SJC']
21171 ['EWR', 'AUS', 'DCA', 'PSP', 'FLL', 'BOS', 'PDX', 'PHL', 'SAN', 'DFW', 'LAX', 'SFO', 'SEA', 'ORD', 'LAS', 'IAD', 'JFK', 'SJC', 'MCO']
19805 ['DFW', 'MIA', 'LGA', 'SLC', 'STL', 'BWI', 'SAN', 'ABQ', 'RNO',

d. O vôo de maior distância de cada companhia

In [13]:
def distancias_por_companhia(line):
    record = line.split(',')
    return (record[1],float(record[10]))

distancias = flights_RDD.map(distancias_por_companhia).collect()
maxDist_RDD = sc.parallelize(distancias).reduceByKey(max).collect()
print(maxDist_RDD)

[('19930', 2874.0), ('20409', 2704.0), ('20366', 1389.0), ('20437', 2139.0), ('19690', 4983.0), ('20355', 2979.0), ('21171', 2704.0), ('19805', 3784.0), ('19790', 4502.0), ('20436', 1703.0), ('20398', 1379.0), ('20304', 1535.0), ('19977', 4962.0), ('19393', 2335.0)]


e. Qual é o vôo mais frequente de cada companhia

In [14]:
voos_frequentes = {}
quantidade_voos_frequentes = {}

def mais_frequente(line):
    record = line.split(',')
    return (record[1], record[2])

voos_mais_frequentes_por_companhia = flights_RDD.map(mais_frequente).take(500000)
voos_mais_frequentes_por_companhia_RDD = sc.parallelize(voos_mais_frequentes_por_companhia)

voos_mais_frequentes_por_companhia_agrupado_RDD = voos_mais_frequentes_por_companhia_RDD.groupByKey().sortByKey()

for i in voos_mais_frequentes_por_companhia_agrupado_RDD.collect():
    voos_frequentes[i[0]] = list(i[1])
    
for companhia in voos_frequentes.keys():
    for id_flight in voos_frequentes[companhia]:
        if id_flight in quantidade_voos_frequentes:
            quantidade_voos_frequentes[id_flight] += 1
        else:
            quantidade_voos_frequentes[id_flight] = 1
            
    quantidade_de_voos = int(max(quantidade_voos_frequentes.values()))
    id_do_voo = list(quantidade_voos_frequentes.keys())[list(quantidade_voos_frequentes.values()).index(quantidade_de_voos)]
    quantidade_voos_frequentes.clear()
    
    print(f'O voo mais frequente da companhia: {companhia} é {id_do_voo} com {quantidade_de_voos} voos')

O voo mais frequente da companhia: 19393 é 583 com 170 voos
O voo mais frequente da companhia: 19690 é 1 com 30 voos
O voo mais frequente da companhia: 19790 é 1258 com 60 voos
O voo mais frequente da companhia: 19805 é 29 com 60 voos
O voo mais frequente da companhia: 19930 é 64 com 150 voos
O voo mais frequente da companhia: 19977 é 1246 com 75 voos
O voo mais frequente da companhia: 20304 é 5325 com 90 voos
O voo mais frequente da companhia: 20355 é 409 com 120 voos
O voo mais frequente da companhia: 20366 é 2514 com 60 voos
O voo mais frequente da companhia: 20398 é 2726 com 60 voos
O voo mais frequente da companhia: 20409 é 2054 com 59 voos
O voo mais frequente da companhia: 20436 é 143 com 50 voos
O voo mais frequente da companhia: 20437 é 221 com 46 voos
O voo mais frequente da companhia: 21171 é 251 com 60 voos


### 2. Utilizando o dataset shakespeare.txt, faça uma operação de MapReduce para construir um índice invertido contendo como chave cada palavra e como valor uma lista de linhas onde ela foi mecionada.

In [18]:
def busca_frase(frase):
  frase = frase.split('\t', 1)
  for palavra in frase[1].strip().replace('\t', ' ').split():
    yield palavra, frase[0].split('@')[1]

shakespeare_file = '/content/shakespeare.txt'
shakespeare_RDD = sc.textFile(shakespeare_file)
palavras_RDD = shakespeare_RDD.flatMap(busca_frase).groupByKey()

for palavra, frases in palavras_RDD.collect():
  print(f'Palavra: {palavra}, linhas encontradas: {list(frases)}')

Palavra: PERSONAE, linhas encontradas: ['10', '20', '15', '13', '24', '24', '19', '13', '11', '16', '19', '19', '22', '21', '19', '20', '29', '19', '19', '30', '23', '24', '18', '27', '20', '26', '26', '14', '17', '18', '20', '28', '11', '31', '15', '29', '24']
Palavra: CLAUDIUS, linhas encontradas: ['31', '9319', '11141', '11924', '12169', '12374', '13347', '14869', '46783', '48245', '48765', '49120', '49283', '49560', '50654', '52845', '52955', '53935', '54145', '54379', '54824', '75150', '76257', '76504', '77527', '77847', '82797', '82837', '84001', '88803', '88961', '95686', '95833', '97366', '103001', '104042', '104698', '107425', '118128', '118410', '118718', '119406', '121864', '122485', '122580', '122699', '122764', '123127', '123265', '123400', '123663', '123777', '124126', '124167', '124309', '124480', '130225', '130415', '130812', '131174', '131522', '132631', '133316', '133914', '134287', '134340', '134693', '134843', '135070', '135238', '137465', '138183', '140054', '14009

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



A saída de streaming foi truncada nas últimas 5000 linhas.
Palavra: asleep--, linhas encontradas: ['23375']
Palavra: Soundly, linhas encontradas: ['23469']
Palavra: fume,, linhas encontradas: ['23592']
Palavra: limbeck, linhas encontradas: ['23636']
Palavra: drenched, linhas encontradas: ['23675', '30815']
Palavra: quell?, linhas encontradas: ['23842']
Palavra: men-children, linhas encontradas: ['23864']
Palavra: only;, linhas encontradas: ['23864']
Palavra: males., linhas encontradas: ['23944']
Palavra: a-bed:, linhas encontradas: ['25069']
Palavra: kind'st, linhas encontradas: ['25687']
Palavra: franchised, linhas encontradas: ['25870']
Palavra: counsell'd., linhas encontradas: ['25913']
Palavra: FLEANCE], linhas encontradas: ['26008']
Palavra: vision,, linhas encontradas: ['26292', '75344', '77178', '61656']
Palavra: creation,, linhas encontradas: ['26371']
Palavra: Proceeding, linhas encontradas: ['26412']
Palavra: dudgeon, linhas encontradas: ['26702']
Palavra: informs, linhas enc

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



A saída de streaming foi truncada nas últimas 5000 linhas.
Palavra: stay'd!, linhas encontradas: ['8311']
Palavra: insane, linhas encontradas: ['8412']
Palavra: Cawdor:, linhas encontradas: ['9365', '10773']
Palavra: thane!, linhas encontradas: ['9415']
Palavra: robes?, linhas encontradas: ['9592']
Palavra: capital,, linhas encontradas: ['9903']
Palavra: oftentimes,, linhas encontradas: ['10343']
Palavra: truths,, linhas encontradas: ['10383']
Palavra: theme.--I, linhas encontradas: ['10602']
Palavra: soliciting, linhas encontradas: ['10652']
Palavra: imaginings:, linhas encontradas: ['10988']
Palavra: partner's, linhas encontradas: ['11182']
Palavra: MACBETH,, linhas encontradas: ['12738', '14897', '24967', '41974', '42021', '43583', '52665', '52665', '87920', '92291', '96649']
Palavra: deserved,, linhas encontradas: ['12921', '13501']
Palavra: duties;, linhas encontradas: ['13204']
Palavra: enfold, linhas encontradas: ['13548']
Palavra: Malcolm,, linhas encontradas: ['13866', '90734'